#### Importando bibliotecas

In [ ]:
import pandas as pd  #possibilita manipulação e análise de dados
import requests  #possibilita integração com serviços web, solicitações HTTP consumir dados de APIs
import ssl
import certifi
import urllib3
from pymongo import MongoClient

#### Conectando ao MongoDB Atlas

In [ ]:
# Conectar ao MongoDB Atlas
client = MongoClient("")
# Seleciona o banco de dados
db = client[""]
# Seleciona a coleção
collection = db["inpc"]

In [3]:
# Recuperar dados da coleção
data = list(collection.find())
data

[]

In [4]:
# Converter para DataFrame
df = pd.DataFrame(data)
print(df)

Empty DataFrame
Columns: []
Index: []


#### Consumindo API e enviando dados para o banco

In [5]:
# Endpoint da API do IBGE para o agregado de taxa de desocupação
url = "https://servicodados.ibge.gov.br/api/v3/agregados/7063/periodos/202001-202407/variaveis/44|68?localidades=N1[all]&classificacao=315[all]"

# Realizar a requisição
response = requests.get(url)

def process_ibge_json(data):
    # Inicializa as variáveis de hierarquia
    current_group = None
    current_subgrupo = None
    current_item = None
    rows = []

    # Itera sobre cada resultado no JSON
    for resultado in data[0]['resultados']:
        classificacoes = resultado['classificacoes']
        for classificacao in classificacoes:
            for codigo, descricao in classificacao['categoria'].items():
                # Verifica se a descrição contém '.' para hierarquia
                if '.' in descricao:
                    partes = descricao.split('.', 1)
                    prefix = partes[0]
                    nome = partes[1]

                    # Determina o nível hierárquico baseado no comprimento do prefixo
                    if len(prefix) == 1:
                        # Grupo
                        current_group = nome
                    elif len(prefix) == 2:
                        # Subgrupo
                        current_subgrupo = nome
                    elif len(prefix) == 4:
                        # Item
                        current_item = nome
                    elif len(prefix) == 7:
                        # Subitem
                        subitem = nome
                        # Agora, processa a série correspondente
                        for serie in resultado['series']:
                            localidade = serie['localidade']['nome']
                            for periodo, valor in serie['serie'].items():
                                ano = periodo[:4]
                                mes = periodo[4:]
                                try:
                                    valor_float = float(valor)
                                except ValueError:
                                    valor_float = None  # Tratar valores inválidos

                                rows.append({
                                    "Grupo": current_group,
                                    "Subgrupo": current_subgrupo,
                                    "Item": current_item,
                                    "Subitem": subitem,
                                    "Ano": ano,
                                    "Mês": mes,
                                    "Localidade": localidade,
                                    "Valor INPC": valor_float
                                })
                else:
                    # Ignora classificações sem hierarquia (como "Índice geral")
                    continue

    # Cria o DataFrame
    df = pd.DataFrame(rows)

    return df


# Verificar se a requisição foi bem-sucedida
if response.status_code == 200:
  data = response.json()
  print(data)
    # Extrair e organizar os dados
    # Lista para armazenar linhas do DataFrame
    # Lista para armazenar os registros formatados

  df = process_ibge_json(data)


else:
    print("Erro:", response.status_code, response.text)

[{'id': '44', 'variavel': 'INPC - Variação mensal', 'unidade': '%', 'resultados': [{'classificacoes': [{'id': '315', 'nome': 'Geral, grupo, subgrupo, item e subitem', 'categoria': {'7169': 'Índice geral'}}], 'series': [{'localidade': {'id': '1', 'nivel': {'id': 'N1', 'nome': 'Brasil'}, 'nome': 'Brasil'}, 'serie': {'202001': '0.19', '202002': '0.17', '202003': '0.18', '202004': '-0.23', '202005': '-0.25', '202006': '0.30', '202007': '0.44', '202008': '0.36', '202009': '0.87', '202010': '0.89', '202011': '0.95', '202012': '1.46', '202101': '0.27', '202102': '0.82', '202103': '0.86', '202104': '0.38', '202105': '0.96', '202106': '0.60', '202107': '1.02', '202108': '0.88', '202109': '1.20', '202110': '1.16', '202111': '0.84', '202112': '0.73', '202201': '0.67', '202202': '1.00', '202203': '1.71', '202204': '1.04', '202205': '0.45', '202206': '0.62', '202207': '-0.60', '202208': '-0.31', '202209': '-0.32', '202210': '0.47', '202211': '0.38', '202212': '0.69', '202301': '0.46', '202302': '0.

In [6]:
df.sample(20)

Grupo                         Subgrupo  \
16478  Saúde e cuidados pessoais                Serviços de saúde   
15080                Transportes                      Transportes   
13108                  Vestuário                           Roupas   
4730       Alimentação e bebidas         Alimentação no domicílio   
10359                  Habitação           Combustíveis e energia   
15599  Saúde e cuidados pessoais  Produtos farmacêuticos e óticos   
18357          Despesas pessoais                 Recreação e fumo   
7363       Alimentação e bebidas         Alimentação no domicílio   
4145       Alimentação e bebidas         Alimentação no domicílio   
10150                  Habitação            Encargos e manutenção   
19787                Comunicação                      Comunicação   
4206       Alimentação e bebidas         Alimentação no domicílio   
3903       Alimentação e bebidas         Alimentação no domicílio   
2159       Alimentação e bebidas         Alimentação no domicílio   
18167          Despesas pessoais                 Recreação e fumo   
15351                Transportes                      Transportes   
1533       Alimentação e bebidas         Alimentação no domicílio   
15498  Saúde e cuidados pessoais  Produtos farmacêuticos e óticos   
5237       Alimentação e bebidas         Alimentação no domicílio   
5688       Alimentação e bebidas         Alimentação no domicílio   

                                   Item                             Subitem  \
16478      Serviços médicos e dentários                Aparelho ortodôntico   
15080                   Veículo próprio                  Pintura de veículo   
13108                    Roupa infantil            Camisa/camiseta infantil   
4730                           Pescados                    Peixe - tambaqui   
10359         Combustíveis (domésticos)                        Gás encanado   
15599            Produtos farmacêuticos  Anti-inflamatório e antirreumático   
18357                         Recreação            Material de caça e pesca   
7363              Enlatados e conservas                  Pepino em conserva   
4145                           Pescados                   Peixe - cavalinha   
10150                Artigos de limpeza                   Limpador multiuso   
19787                       Comunicação                             Correio   
4206                           Pescados                    Peixe - sardinha   
3903                             Carnes                        Capa de filé   
2159                             Frutas                       Banana - maçã   
18167                         Recreação                           Brinquedo   
15351           Combustíveis (veículos)                         Óleo diesel   
1533               Açúcares e derivados      Chocolate e achocolatado em pó   
15498            Produtos farmacêuticos       Anti-infeccioso e antibiótico   
5237   Carnes e peixes industrializados                 Carne-seca e de sol   
5688                 Leites e derivados                         Leite em pó   

        Ano Mês Localidade  Valor INPC  
16478  2022  10     Brasil        1.50  
15080  2020  11     Brasil       -0.03  
13108  2021  07     Brasil        0.23  
4730   2020  01     Brasil       -1.05  
10359  2021  08     Brasil        1.67  
15599  2022  11     Brasil        1.12  
18357  2023  07     Brasil        0.04  
7363   2024  01     Brasil       -0.04  
4145   2021  09     Brasil       -1.35  
10150  2022  07     Brasil        0.07  
19787  2023  07     Brasil        0.00  
4206   2022  03     Brasil        0.36  
3903   2024  06     Brasil       -2.13  
2159   2021  03     Brasil        9.24  
18167  2021  06     Brasil        1.11  
15351  2020  07     Brasil        4.57  
1533   2024  01     Brasil        0.52  
15498  2023  08     Brasil        0.00  
5237   2021  01     Brasil        1.69  
5688   2021  12     Brasil       -0.30

In [7]:
#tranformar dados em dicionário para insertir no banco de dados
data_dict = df.to_dict("records")
print(data_dict)

[{'Grupo': 'Alimentação e bebidas', 'Subgrupo': 'Alimentação no domicílio', 'Item': 'Cereais, leguminosas e oleaginosas', 'Subitem': 'Arroz', 'Ano': '2020', 'Mês': '01', 'Localidade': 'Brasil', 'Valor INPC': 1.19}, {'Grupo': 'Alimentação e bebidas', 'Subgrupo': 'Alimentação no domicílio', 'Item': 'Cereais, leguminosas e oleaginosas', 'Subitem': 'Arroz', 'Ano': '2020', 'Mês': '02', 'Localidade': 'Brasil', 'Valor INPC': 1.04}, {'Grupo': 'Alimentação e bebidas', 'Subgrupo': 'Alimentação no domicílio', 'Item': 'Cereais, leguminosas e oleaginosas', 'Subitem': 'Arroz', 'Ano': '2020', 'Mês': '03', 'Localidade': 'Brasil', 'Valor INPC': 1.61}, {'Grupo': 'Alimentação e bebidas', 'Subgrupo': 'Alimentação no domicílio', 'Item': 'Cereais, leguminosas e oleaginosas', 'Subitem': 'Arroz', 'Ano': '2020', 'Mês': '04', 'Localidade': 'Brasil', 'Valor INPC': 3.89}, {'Grupo': 'Alimentação e bebidas', 'Subgrupo': 'Alimentação no domicílio', 'Item': 'Cereais, leguminosas e oleaginosas', 'Subitem': 'Arroz', 'A

In [8]:
# Inserindo os dados no MongoDB
collection.insert_many(data_dict)

InsertManyResult([ObjectId('674b9811dfb25fec2ca9b4a0'), ObjectId('674b9811dfb25fec2ca9b4a1'), ObjectId('674b9811dfb25fec2ca9b4a2'), ObjectId('674b9811dfb25fec2ca9b4a3'), ObjectId('674b9811dfb25fec2ca9b4a4'), ObjectId('674b9811dfb25fec2ca9b4a5'), ObjectId('674b9811dfb25fec2ca9b4a6'), ObjectId('674b9811dfb25fec2ca9b4a7'), ObjectId('674b9811dfb25fec2ca9b4a8'), ObjectId('674b9811dfb25fec2ca9b4a9'), ObjectId('674b9811dfb25fec2ca9b4aa'), ObjectId('674b9811dfb25fec2ca9b4ab'), ObjectId('674b9811dfb25fec2ca9b4ac'), ObjectId('674b9811dfb25fec2ca9b4ad'), ObjectId('674b9811dfb25fec2ca9b4ae'), ObjectId('674b9811dfb25fec2ca9b4af'), ObjectId('674b9811dfb25fec2ca9b4b0'), ObjectId('674b9811dfb25fec2ca9b4b1'), ObjectId('674b9811dfb25fec2ca9b4b2'), ObjectId('674b9811dfb25fec2ca9b4b3'), ObjectId('674b9811dfb25fec2ca9b4b4'), ObjectId('674b9811dfb25fec2ca9b4b5'), ObjectId('674b9811dfb25fec2ca9b4b6'), ObjectId('674b9811dfb25fec2ca9b4b7'), ObjectId('674b9811dfb25fec2ca9b4b8'), ObjectId('674b9811dfb25fec2ca9b4

In [ ]:
try:
    client.admin.command('ping')
    print("Conexão com o MongoDB foi bem-sucedida!")
except Exception as e:
    print(f"Erro ao conectar: {e}")